In [ ]:
import pandas as pd
from sqlalchemy import create_engine, Column, Integer, String, Text, Date, Table, ForeignKey
from sqlalchemy.ext.declarative import declarative_base
from sqlalchemy.orm import sessionmaker, relationship

# -------------------------------
# 1. Connect to MySQL
# -------------------------------
username = 'root'
password = '*****'  # Replace with your actual password
host = 'localhost'
port = 3306
database = 'Netflix'

engine = create_engine(f'mysql+mysqlconnector://{username}:{password}@{host}:{port}/{database}', echo=True)
Session = sessionmaker(bind=engine)
session = Session()
Base = declarative_base()

# -------------------------------
# 2. Define ORM Classes
# -------------------------------
class Genre(Base):
    __tablename__ = 'Genres'
    Genre_id = Column(Integer, primary_key=True, autoincrement=True)
    Genre_name = Column(String(100), unique=True, nullable=False)

class CastMember(Base):
    __tablename__ = 'Cast_Members'
    Cast_id = Column(Integer, primary_key=True, autoincrement=True)
    Cast_name = Column(String(255), nullable=False)

class Country(Base):
    __tablename__ = 'Countries'
    Country_id = Column(Integer, primary_key=True, autoincrement=True)
    Country_name = Column(String(100), unique=True, nullable=False)

class Director(Base):
    __tablename__ = 'Directors'
    Director_id = Column(Integer, primary_key=True, autoincrement=True)
    Director_Name = Column(String(255), nullable=False)

class Show(Base):
    __tablename__ = 'Shows'
    Show_id = Column(String(20), primary_key=True)
    Title = Column(String(500), nullable=False)
    Type = Column(String(20))
    Description = Column(Text)
    Duration = Column(String(50))
    Rating = Column(String(20))
    Data_Added = Column(Date)
    Release_Date = Column(Integer)

# Mapping tables
class Listed(Base):
    __tablename__ = 'Listed'
    Show_id = Column(String(20), ForeignKey('Shows.Show_id', ondelete='CASCADE'), primary_key=True)
    Genre_id = Column(Integer, ForeignKey('Genres.Genre_id', ondelete='CASCADE'), primary_key=True)

class ShowsCast(Base):
    __tablename__ = 'Shows_Cast'
    Show_id = Column(String(20), ForeignKey('Shows.Show_id', ondelete='CASCADE'), primary_key=True)
    Cast_id = Column(Integer, ForeignKey('Cast_Members.Cast_id', ondelete='CASCADE'), primary_key=True)

class Producer(Base):
    __tablename__ = 'Producer'
    Show_id = Column(String(20), ForeignKey('Shows.Show_id', ondelete='CASCADE'), primary_key=True)
    Director_id = Column(Integer, ForeignKey('Directors.Director_id', ondelete='CASCADE'), primary_key=True)

class MadeIn(Base):
    __tablename__ = 'Made_in'
    Show_id = Column(String(20), ForeignKey('Shows.Show_id', ondelete='CASCADE'), primary_key=True)
    Country_id = Column(Integer, ForeignKey('Countries.Country_id', ondelete='CASCADE'), primary_key=True)

# -------------------------------
# 3. Load CSV
# -------------------------------
df = pd.read_csv('netflix_titles_cleaned.csv')

# -------------------------------
# 4. Helper: Insert unique reference data
# -------------------------------
def get_or_create(session, model, value, column_name):
    instance = session.query(model).filter(getattr(model, column_name)==value).first()
    if instance:
        return instance
    else:
        instance = model(**{column_name: value})
        session.add(instance)
        session.commit()
        return instance

# -------------------------------
# 5. Insert Data
# -------------------------------
for _, row in df.iterrows():
    # Insert Show
    show = Show(
        Show_id=str(row['show_id']),
        Title=row['title'],
        Type=row['type'],
        Description=row['description'] if 'description' in row else None,
        Duration=row['duration'],
        Rating=row['rating'],
        Data_Added=pd.to_datetime(row['date_added']) if 'date_added' in row else None,
        Release_Date=row['release_year'] if 'release_year' in row else None
    )
    session.add(show)
    session.commit()

    # Genres (split by comma if multiple)
    if pd.notna(row['listed_in']):
        genres = [g.strip() for g in row['listed_in'].split(',')]
        for g in genres:
            genre = get_or_create(session, Genre, g, 'Genre_name')
            session.add(Listed(Show_id=show.Show_id, Genre_id=genre.Genre_id))

    # Cast Members
    if pd.notna(row['cast']):
        casts = [c.strip() for c in row['cast'].split(',')]
        for c in casts:
            cast_member = get_or_create(session, CastMember, c, 'Cast_name')
            session.add(ShowsCast(Show_id=show.Show_id, Cast_id=cast_member.Cast_id))

    # Directors
    if pd.notna(row['director']):
        directors = [d.strip() for d in row['director'].split(',')]
        for d in directors:
            director = get_or_create(session, Director, d, 'Director_Name')
            session.add(Producer(Show_id=show.Show_id, Director_id=director.Director_id))

    # Countries
    if pd.notna(row['country']):
        countries = [c.strip() for c in row['country'].split(',')]
        for c in countries:
            country = get_or_create(session, Country, c, 'Country_name')
            session.add(MadeIn(Show_id=show.Show_id, Country_id=country.Country_id))

    session.commit()

session.close()
print("✅ All data inserted successfully!")


C:\Users\LEGION\AppData\Local\Temp\ipykernel_14008\3039052630.py:18: MovedIn20Warning: The ``declarative_base()`` function is now available as sqlalchemy.orm.declarative_base(). (deprecated since: 2.0) (Background on SQLAlchemy 2.0 at: https://sqlalche.me/e/b8d9)
  Base = declarative_base()


2026-02-06 22:51:02,150 INFO sqlalchemy.engine.Engine SELECT DATABASE()
2026-02-06 22:51:02,152 INFO sqlalchemy.engine.Engine [raw sql] {}
2026-02-06 22:51:02,154 INFO sqlalchemy.engine.Engine SELECT @@sql_mode
2026-02-06 22:51:02,154 INFO sqlalchemy.engine.Engine [raw sql] {}
2026-02-06 22:51:02,155 INFO sqlalchemy.engine.Engine SELECT @@lower_case_table_names
2026-02-06 22:51:02,155 INFO sqlalchemy.engine.Engine [raw sql] {}
2026-02-06 22:51:02,157 INFO sqlalchemy.engine.Engine BEGIN (implicit)
2026-02-06 22:51:02,158 INFO sqlalchemy.engine.Engine INSERT INTO `Shows` (`Show_id`, `Title`, `Type`, `Description`, `Duration`, `Rating`, `Data_Added`, `Release_Date`) VALUES (%(Show_id)s, %(Title)s, %(Type)s, %(Description)s, %(Duration)s, %(Rating)s, %(Data_Added)s, %(Release_Date)s)
2026-02-06 22:51:02,159 INFO sqlalchemy.engine.Engine [generated in 0.00071s] {'Show_id': 's1', 'Title': 'Dick Johnson Is Dead', 'Type': 'Movie', 'Description': 'As her father nears the end of his life, filmma